# Plots With Additional Scores Plus RPC

In [ ]:
import glob
import itertools
import numpy as np
import os
import sys
import time
import tqdm

from typing import Any, Callable, List, Dict

import matplotlib.pyplot as plt

%matplotlib inline

In [ ]:
sys.path.insert(0, '../../OptimalNumberOfTopics/')     # topnum
sys.path.insert(1, '../..')  # topicnet

In [ ]:
import warnings

warnings.filterwarnings("ignore", category=UserWarning)

In [ ]:
from topicnet.cooking_machine.models import TopicModel
from topicnet.cooking_machine.models.dummy_topic_model import DummyTopicModel
from topicnet.cooking_machine.dataset import Dataset

from topicnet.cooking_machine.models import scores as tn_scores

from topnum.data.vowpal_wabbit_text_collection import VowpalWabbitTextCollection
from topnum.search_methods.optimize_scores_method import (
    OptimizeScoresMethod,
    load_models_from_disk,
)
from topnum.utils import (
    read_corpus_config, split_into_train_test, 
    build_every_score, monotonity_and_std_analysis, 
    trim_config, plot_everything_informative
)
from topnum.model_constructor import KnownModel, PARAMS_EXPLORED
from topnum.utils import estimate_num_iterations_for_convergence

## Loading "Ordinary" Scores

Experiments directory

In [ ]:
! ls /data/_tmp_alekseev/OptNumExperiments/AllDatasets

20NG_20NG_NEW	 PN_PN_NEW	      SO_SO_NEW
Brown_Brown_NEW  Reuters_Reuters_NEW  WRef_NEW


In [ ]:
! ls /data/_tmp_alekseev/OptNumExperiments/AllDatasets/WRef_NEW

WRef_test_ARTM_0_0   WRef_test_ARTM_6_0		  WRef_test_LDA_1_0
WRef_test_ARTM_0_1   WRef_test_ARTM_6_1		  WRef_test_LDA_1_1
WRef_test_ARTM_0_2   WRef_test_ARTM_6_2		  WRef_test_LDA_1_2
WRef_test_ARTM_1_0   WRef_test_ARTM_7_0		  WRef_test_LDA_2_0
WRef_test_ARTM_10_0  WRef_test_ARTM_7_1		  WRef_test_LDA_2_1
WRef_test_ARTM_10_1  WRef_test_ARTM_7_2		  WRef_test_LDA_2_2
WRef_test_ARTM_10_2  WRef_test_ARTM_8_0		  WRef_test_PLSA_0_0
WRef_test_ARTM_1_1   WRef_test_ARTM_8_1		  WRef_test_PLSA_0_1
WRef_test_ARTM_11_0  WRef_test_ARTM_8_2		  WRef_test_PLSA_0_2
WRef_test_ARTM_11_1  WRef_test_ARTM_9_0		  WRef_test_sparse_0_0
WRef_test_ARTM_11_2  WRef_test_ARTM_9_1		  WRef_test_sparse_0_1
WRef_test_ARTM_1_2   WRef_test_ARTM_9_2		  WRef_test_sparse_0_2
WRef_test_ARTM_2_0   WRef_test_decorrelation_0_0  WRef_test_sparse_1_0
WRef_test_ARTM_2_1   WRef_test_decorrelation_0_1  WRef_test_sparse_1_1
WRef_test_ARTM_2_2   WRef_test_decorrelation_0_2  WRef_test_sparse_1_2
WRef_test_ARTM_3_0   WRef_test_decorrelatio

In [ ]:
EXPERIMENT_DIRECTORY = os.path.join(
    f'/data/_tmp_alekseev/OptNumExperiments/AllDatasets',
    f'WRef_NEW'
)
EXPERIMENT_NAME_TEMPLATE = "WRef_test_{mfv}_{param_id}_{seed}"
OLD_EXPERIMENT_NAME_TEMPLATE = "WRef_test_{}_{}"


for model_family in KnownModel:
    print(model_family)

    template = EXPERIMENT_NAME_TEMPLATE.format(
        mfv=model_family.value, param_id="{}", seed="{}"
    )
    all_models_mask = os.path.join(
        EXPERIMENT_DIRECTORY,
        EXPERIMENT_NAME_TEMPLATE.format(mfv=model_family.value, param_id="*", seed="*")
    )

    for entry in glob.glob(all_models_mask):
        model_kin = os.path.basename(entry)
        *rest, mfv, params_id, seed = model_kin.split("_")

        print(model_kin, params_id)

KnownModel.LDA
WRef_test_LDA_2_0 2
WRef_test_LDA_1_2 1
WRef_test_LDA_2_2 2
WRef_test_LDA_1_0 1
WRef_test_LDA_0_2 0
WRef_test_LDA_1_1 1
WRef_test_LDA_0_0 0
WRef_test_LDA_2_1 2
WRef_test_LDA_0_1 0
KnownModel.PLSA
WRef_test_PLSA_0_1 0
WRef_test_PLSA_0_0 0
WRef_test_PLSA_0_2 0
KnownModel.SPARSE
WRef_test_sparse_1_1 1
WRef_test_sparse_2_2 2
WRef_test_sparse_3_2 3
WRef_test_sparse_1_0 1
WRef_test_sparse_2_1 2
WRef_test_sparse_3_1 3
WRef_test_sparse_2_0 2
WRef_test_sparse_3_0 3
WRef_test_sparse_0_0 0
WRef_test_sparse_0_2 0
WRef_test_sparse_1_2 1
WRef_test_sparse_0_1 0
KnownModel.TLESS
WRef_test_TARTM_0_2 0
WRef_test_TARTM_0_0 0
WRef_test_TARTM_0_1 0
KnownModel.DECORRELATION
WRef_test_decorrelation_1_1 1
WRef_test_decorrelation_0_2 0
WRef_test_decorrelation_2_0 2
WRef_test_decorrelation_0_0 0
WRef_test_decorrelation_1_2 1
WRef_test_decorrelation_2_1 2
WRef_test_decorrelation_0_1 0
WRef_test_decorrelation_2_2 2
WRef_test_decorrelation_1_0 1
KnownModel.ARTM
WRef_test_ARTM_1_1 1
WRef_test_ARTM_9_

## Plot Functions

In [ ]:
KEY_SCORE_VALUES = 'score_values'
KEY_NUM_TOPICS_VALUES = 'num_topics_values'

In [ ]:
def plot_all_the_plots(
        score_names,
        model_names,
        model_results,
        errorbar=True,
        fix_arun=False):

    XLABEL = 'Num topics'
    MARKER_SIZE = 10
    MARKER = '.'
    
    nrows = len(score_names)
    ncols = len(model_names)

    fig, axes = plt.subplots(
        nrows=nrows,
        ncols=ncols,
        figsize=(5 * ncols, 4 * nrows)
    )

    for i, score_name in enumerate(score_names):
        for j, model_name in enumerate(model_names):
            score_values = np.array([
                np.array(model_results[model_name][restart_num][score_name][KEY_SCORE_VALUES])
                for restart_num in MODEL_RESULTS[model_name]
            ])
            num_topics_values = np.array([
                np.array(model_results[model_name][restart_num][score_name][KEY_NUM_TOPICS_VALUES])
                for restart_num in MODEL_RESULTS[model_name]
            ])

            # TODO: kostyl, need this for Synthetic datasets
            if fix_arun and score_name == 'arun':
                for s in score_values:
                    s[np.where(s == 0)] = 1
    
            # TODO: probably this shouldn't be here
            if not np.all(num_topics_values == num_topics_values[0, :]):
                sort_indices = np.argsort(num_topics_values, axis=1)

                num_topics_values = np.take_along_axis(
                    num_topics_values, sort_indices, axis=1
                )
                score_values = np.take_along_axis(
                    score_values, sort_indices, axis=1
                )            
            
            assert np.all(num_topics_values == num_topics_values[0, :]) 

            if not errorbar:
                for x, y in zip(num_topics_values, score_values):
                    axes[i, j].plot(x, y, ms=MARKER_SIZE, marker=MARKER)
            else:
                x = num_topics_values[0]
                y = np.mean(score_values, axis=0)
                yerr = 1.0 / 2 * (np.max(score_values, axis=0) - np.min(score_values, axis=0))

                axes[i, j].errorbar(
                    x, y, yerr=yerr, ms=MARKER_SIZE, marker=MARKER
                )

    #         if i == 0:
            axes[i, j].set_title(model_name)

    #         if j == 0:
            axes[i, j].set_ylabel(score_name)

            if i == nrows - 1:
                axes[i, j].set_xlabel(XLABEL)

    return fig, axes

In [ ]:
MODEL_RESULTS = dict()

In [ ]:
def load_additional_scores(additional_score_names: List[str]):
    for additional_score_name in additional_score_names:
    
        score_data = dict()
        score_data[KEY_SCORE_VALUES] = list()
        score_data[KEY_NUM_TOPICS_VALUES] = list()
        
        for model_folder_name in os.listdir(entry):

            model_folder_path = os.path.join(entry, model_folder_name)

            target_score_names = [
                s for s in os.listdir(model_folder_path)
                if s.startswith(additional_score_name + '.')
            ]
            
            assert len(target_score_names) == 1
            
            score_name = target_score_names[0]

            score_path = os.path.join(
                model_folder_path,
                score_name
            )

            score_file_name = score_name
            *score_name, score_cls_name, _ = score_file_name.split('.')
            score_name = '.'.join(score_name)

            score_cls = getattr(tn_scores, score_cls_name)
            loaded_score = score_cls.load(score_path)
            # TODO check what happens with score name
            loaded_score._name = score_name

            score_value = loaded_score.value[-1]

            topic_model = DummyTopicModel.load(model_folder_path)
            num_topics_value = len(topic_model.topic_names)

            score_data[KEY_SCORE_VALUES].append(score_value)
            score_data[KEY_NUM_TOPICS_VALUES].append(num_topics_value)

        MODEL_RESULTS[model_name][restart_number][additional_score_name] = score_data

## Import of the Additional Scores

In [ ]:
from topnum.scores import (
    HoldoutPerplexityScore,
    MeanLiftScore,
    UniformThetaDivergenceScore,
)

# Just some dataset, whatever
test_dataset = Dataset('../../topicnet/tests/test_data/test_dataset.csv')

# If not itialize a new score at least once in the notebook
# it won't be possible to load it
_ = HoldoutPerplexityScore('', test_dataset,)
_ = MeanLiftScore('', test_dataset, [])
_ = UniformThetaDivergenceScore('', test_dataset, [])

In [ ]:
ALL_SUBEXPERIMENT_MASK = os.path.join(
    EXPERIMENT_DIRECTORY,
    OLD_EXPERIMENT_NAME_TEMPLATE.format('*', '*'),
)

In [ ]:
ALL_SUBEXPERIMENT_MASK

'/data/_tmp_alekseev/OptNumExperiments/AllDatasets/WRef_NEW/WRef_test_*_*'

In [ ]:
# Names should match the names of the saved scores!

ADDITIONAL_SCORE_NAMES = [
    'new_holdout_perp',
    'lift',
    'uni_theta_divergence',
]

In [ ]:
entries = list(glob.glob(ALL_SUBEXPERIMENT_MASK))

for entry in tqdm.tqdm(entries, total=len(entries)):
    experiment_name = entry.split("/")[-1]
    
    # TODO: kostyl for WRef ("WRef_test_...")
    if not experiment_name.startswith('WRef'):
        _, model_name_prefix, model_name_suffix, restart_number = experiment_name.split('_')
    else:
        _, _, model_name_prefix, model_name_suffix, restart_number = experiment_name.split('_')
    
    model_name = model_name_prefix + '_' + model_name_suffix
    restart_number = int(restart_number)

    result, detailed_result = load_models_from_disk(
        EXPERIMENT_DIRECTORY, experiment_name
    )
    
    if model_name not in MODEL_RESULTS:
        MODEL_RESULTS[model_name] = dict()
    
    MODEL_RESULTS[model_name][restart_number] = result['score_results']
    
    load_additional_scores(ADDITIONAL_SCORE_NAMES)

100%|██████████| 72/72 [01:14<00:00,  1.03s/it]


Let's look what we have

In [ ]:
MODEL_RESULTS.keys()

dict_keys(['decorrelation_1', 'ARTM_1', 'ARTM_9', 'sparse_1', 'ARTM_7', 'decorrelation_0', 'LDA_2', 'decorrelation_2', 'LDA_1', 'sparse_2', 'sparse_3', 'TARTM_0', 'PLSA_0', 'LDA_0', 'ARTM_5', 'ARTM_11', 'ARTM_3', 'ARTM_0', 'ARTM_4', 'ARTM_2', 'ARTM_10', 'ARTM_6', 'ARTM_8', 'sparse_0'])

In [ ]:
MODEL_RESULTS['sparse_1'].keys()

dict_keys([1, 0, 2])

In [ ]:
MODEL_RESULTS['sparse_1'][0].keys()

dict_keys(['PerplexityScore@all', 'SparsityThetaScore', 'SparsityPhiScore@lemmatized', 'PerplexityScore@lemmatized', 'TopicKernel@lemmatized.average_coherence', 'TopicKernel@lemmatized.average_contrast', 'TopicKernel@lemmatized.average_purity', 'TopicKernel@lemmatized.average_size', 'perp', 'sparsity_phi', 'sparsity_theta', 'holdout_perp', 'arun', 'diversity_euclidean_True', 'diversity_euclidean_False', 'diversity_jensenshannon_True', 'diversity_jensenshannon_False', 'diversity_cosine_True', 'diversity_cosine_False', 'diversity_hellinger_True', 'diversity_hellinger_False', 'calhar', 'silh', 'renyi_0.5', 'renyi_1', 'renyi_2', 'AIC_sparsity_True', 'AIC_sparsity_False', 'BIC_sparsity_True', 'BIC_sparsity_False', 'MDL_sparsity_True', 'MDL_sparsity_False', 'intra', 'toptok1', 'new_holdout_perp', 'lift', 'uni_theta_divergence'])

One of the default "ordinary" scores

In [ ]:
MODEL_RESULTS['sparse_1'][0]['PerplexityScore@all']

{'optimum': 3.0,
 'optimum_std': nan,
 'num_topics_values': [3,
  4,
  5,
  6,
  7,
  8,
  9,
  10,
  11,
  12,
  13,
  14,
  15,
  16,
  17,
  18,
  19,
  20,
  21],
 'score_values': [1498.4991455078125,
  1399.9892578125,
  1200.2041015625,
  1148.9871826171875,
  1075.0711669921875,
  1057.8624267578125,
  976.9273681640625,
  923.9677124023438,
  901.0869140625,
  879.1796875,
  880.8346557617188,
  850.8522338867188,
  825.9130859375,
  828.6478881835938,
  789.720703125,
  775.0276489257812,
  752.7982788085938,
  742.4148559570312,
  727.8945922851562],
 'score_values_std': [nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  nan,
  nan]}

And one of the additional scores

In [ ]:
MODEL_RESULTS['sparse_1'][0]['new_holdout_perp']

{'score_values': [1160.0975341796875,
  1173.891357421875,
  1359.7489013671875,
  1162.41357421875,
  1165.633544921875,
  1168.490234375,
  1770.328857421875,
  1127.0848388671875,
  1121.9100341796875,
  1115.8531494140625,
  1289.73779296875,
  1153.857421875,
  1692.7335205078125,
  1210.4326171875,
  1131.8663330078125,
  1134.8177490234375,
  1392.439453125,
  1114.3306884765625,
  1299.296142578125],
 'num_topics_values': [11,
  16,
  6,
  14,
  13,
  10,
  3,
  17,
  19,
  20,
  8,
  12,
  4,
  9,
  18,
  15,
  5,
  21,
  7]}

## RPC (A Score Over Scores)

In [ ]:
def compute_meta_scores(meta_scores: Dict[str, Callable[[dict], float]]):
    for meta_score_name, meta_score_compute in meta_scores.items():
        for model_name, model_results in MODEL_RESULTS.items():
            for restart_number, restart_results in model_results.items():
                restart_results[meta_score_name] = meta_score_compute(restart_results)

In [ ]:
PEPLEXITY_SCORE_NAME = 'perp'

def compute_rpc(computed_scores: Dict[str, Dict[str, Any]]) -> float:
    num_topics_values = computed_scores[PEPLEXITY_SCORE_NAME][KEY_NUM_TOPICS_VALUES]
    
    score_values = _compute_rpc(
        perplexity_score_values=computed_scores[PEPLEXITY_SCORE_NAME][KEY_SCORE_VALUES],
        iterations=num_topics_values
    )
    
    return {
        KEY_SCORE_VALUES: score_values,
        KEY_NUM_TOPICS_VALUES: num_topics_values
    }

def _compute_rpc(
        perplexity_score_values: List[float],
        iterations: List[int] = None) -> List[float]:
    """
    If `iterations` is `None`, each steps is assumed to be equal `1`.
    """

    if iterations is None:
        iterations = list(range(1, len(perplexity_score_values) + 1))
    else:
        assert iterations == sorted(iterations)  # TODO: may be time consuming here

    assert iterations[0] > 0

    # TODO: optimize? can't append inf of nan in np.ediff1d
    result = [perplexity_score_values[0] - float('+inf')] + list(np.ediff1d(perplexity_score_values))
    result = np.array(result)

    iterations = [iterations[0] - 0] + list(np.ediff1d(iterations))

    return list(
        result / iterations
    )

In [ ]:
# test

_compute_rpc([1, 2, 3])

[-inf, 1.0, 1.0]

In [ ]:
# test

compute_rpc(MODEL_RESULTS['sparse_1'][0])

{'score_values': [-inf,
  -98.5098876953125,
  -199.78515625,
  -51.2169189453125,
  -73.916015625,
  -17.208740234375,
  -80.93505859375,
  -52.95965576171875,
  -22.88079833984375,
  -21.9072265625,
  1.65496826171875,
  -29.982421875,
  -24.93914794921875,
  2.73480224609375,
  -38.92718505859375,
  -14.69305419921875,
  -22.2293701171875,
  -10.3834228515625,
  -14.520263671875],
 'num_topics_values': [3,
  4,
  5,
  6,
  7,
  8,
  9,
  10,
  11,
  12,
  13,
  14,
  15,
  16,
  17,
  18,
  19,
  20,
  21]}

What meta scores to compute

In [ ]:
META_SCORES: Dict[str, Callable] = {
    'rpc': compute_rpc
}

Compute meta scores!

In [ ]:
compute_meta_scores(META_SCORES)

What we have now

In [ ]:
MODEL_RESULTS['sparse_1'][0].keys()

dict_keys(['PerplexityScore@all', 'SparsityThetaScore', 'SparsityPhiScore@lemmatized', 'PerplexityScore@lemmatized', 'TopicKernel@lemmatized.average_coherence', 'TopicKernel@lemmatized.average_contrast', 'TopicKernel@lemmatized.average_purity', 'TopicKernel@lemmatized.average_size', 'perp', 'sparsity_phi', 'sparsity_theta', 'holdout_perp', 'arun', 'diversity_euclidean_True', 'diversity_euclidean_False', 'diversity_jensenshannon_True', 'diversity_jensenshannon_False', 'diversity_cosine_True', 'diversity_cosine_False', 'diversity_hellinger_True', 'diversity_hellinger_False', 'calhar', 'silh', 'renyi_0.5', 'renyi_1', 'renyi_2', 'AIC_sparsity_True', 'AIC_sparsity_False', 'BIC_sparsity_True', 'BIC_sparsity_False', 'MDL_sparsity_True', 'MDL_sparsity_False', 'intra', 'toptok1', 'new_holdout_perp', 'lift', 'uni_theta_divergence', 'rpc'])

In [ ]:
MODEL_RESULTS['sparse_1'][0]['rpc']

{'score_values': [-inf,
  -98.5098876953125,
  -199.78515625,
  -51.2169189453125,
  -73.916015625,
  -17.208740234375,
  -80.93505859375,
  -52.95965576171875,
  -22.88079833984375,
  -21.9072265625,
  1.65496826171875,
  -29.982421875,
  -24.93914794921875,
  2.73480224609375,
  -38.92718505859375,
  -14.69305419921875,
  -22.2293701171875,
  -10.3834228515625,
  -14.520263671875],
 'num_topics_values': [3,
  4,
  5,
  6,
  7,
  8,
  9,
  10,
  11,
  12,
  13,
  14,
  15,
  16,
  17,
  18,
  19,
  20,
  21]}

In [ ]:
MODEL_RESULTS.keys()

dict_keys(['decorrelation_1', 'ARTM_1', 'ARTM_9', 'sparse_1', 'ARTM_7', 'decorrelation_0', 'LDA_2', 'decorrelation_2', 'LDA_1', 'sparse_2', 'sparse_3', 'TARTM_0', 'PLSA_0', 'LDA_0', 'ARTM_5', 'ARTM_11', 'ARTM_3', 'ARTM_0', 'ARTM_4', 'ARTM_2', 'ARTM_10', 'ARTM_6', 'ARTM_8', 'sparse_0'])

## Plots

In [ ]:
ALL_MODELS = sorted(list(MODEL_RESULTS.keys()))

In [ ]:
ALL_MODELS[:10]

['ARTM_0',
 'ARTM_1',
 'ARTM_10',
 'ARTM_11',
 'ARTM_2',
 'ARTM_3',
 'ARTM_4',
 'ARTM_5',
 'ARTM_6',
 'ARTM_7']

In [ ]:
MODEL_RESULTS['ARTM_0'].keys()

dict_keys([1, 2, 0])

In [ ]:
MODEL_RESULTS['ARTM_0'][0].keys()

dict_keys(['PerplexityScore@all', 'SparsityThetaScore', 'SparsityPhiScore@lemmatized', 'PerplexityScore@lemmatized', 'TopicKernel@lemmatized.average_coherence', 'TopicKernel@lemmatized.average_contrast', 'TopicKernel@lemmatized.average_purity', 'TopicKernel@lemmatized.average_size', 'perp', 'sparsity_phi', 'sparsity_theta', 'holdout_perp', 'arun', 'diversity_euclidean_True', 'diversity_euclidean_False', 'diversity_jensenshannon_True', 'diversity_jensenshannon_False', 'diversity_cosine_True', 'diversity_cosine_False', 'diversity_hellinger_True', 'diversity_hellinger_False', 'calhar', 'silh', 'renyi_0.5', 'renyi_1', 'renyi_2', 'AIC_sparsity_True', 'AIC_sparsity_False', 'BIC_sparsity_True', 'BIC_sparsity_False', 'MDL_sparsity_True', 'MDL_sparsity_False', 'intra', 'toptok1', 'new_holdout_perp', 'lift', 'uni_theta_divergence', 'rpc'])

In [ ]:
ALL_SCORES = sorted(list(MODEL_RESULTS['ARTM_0'][0].keys()))

In [ ]:
ALL_SCORES

['AIC_sparsity_False',
 'AIC_sparsity_True',
 'BIC_sparsity_False',
 'BIC_sparsity_True',
 'MDL_sparsity_False',
 'MDL_sparsity_True',
 'PerplexityScore@all',
 'PerplexityScore@lemmatized',
 'SparsityPhiScore@lemmatized',
 'SparsityThetaScore',
 'TopicKernel@lemmatized.average_coherence',
 'TopicKernel@lemmatized.average_contrast',
 'TopicKernel@lemmatized.average_purity',
 'TopicKernel@lemmatized.average_size',
 'arun',
 'calhar',
 'diversity_cosine_False',
 'diversity_cosine_True',
 'diversity_euclidean_False',
 'diversity_euclidean_True',
 'diversity_hellinger_False',
 'diversity_hellinger_True',
 'diversity_jensenshannon_False',
 'diversity_jensenshannon_True',
 'holdout_perp',
 'intra',
 'lift',
 'new_holdout_perp',
 'perp',
 'renyi_0.5',
 'renyi_1',
 'renyi_2',
 'rpc',
 'silh',
 'sparsity_phi',
 'sparsity_theta',
 'toptok1',
 'uni_theta_divergence']

In [ ]:
ADDITIONAL_SCORE_NAMES

['new_holdout_perp', 'lift', 'uni_theta_divergence']

Reordering scores (for further plots)

In [ ]:
ALL_SCORES.remove('perp')

for s in ADDITIONAL_SCORE_NAMES:
    ALL_SCORES.remove(s)

for s in META_SCORES:
    ALL_SCORES.remove(s)

ALL_SCORES = ALL_SCORES + ['perp'] + ADDITIONAL_SCORE_NAMES + list(META_SCORES.keys())

In [ ]:
ALL_SCORES[-5:]

['perp', 'new_holdout_perp', 'lift', 'uni_theta_divergence', 'rpc']

Checking that all OK

In [ ]:
assert all(
    sorted(list(MODEL_RESULTS[m][0].keys())) == sorted(ALL_SCORES)
    for m in ALL_MODELS
)

In [ ]:
len(ALL_SCORES), len(ALL_MODELS)

(38, 24)

And finally...

In [ ]:
fig, axes = plot_all_the_plots(
    score_names=ALL_SCORES,
    model_names=ALL_MODELS,
    model_results=MODEL_RESULTS,
)

plt.show()

/data/topicnet/lib/python3.6/site-packages/ipykernel_launcher.py:56: RuntimeWarning: invalid value encountered in subtract
